<a href="https://colab.research.google.com/github/RafsanJany-44/Machine-School/blob/main/LIME.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Local  Interpretable Model-agnostic Explanations

In [1]:
!pip install interpret

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [2]:
import pandas as pd
import numpy as np

In [3]:
data = 'https://raw.githubusercontent.com/RafsanJany-44/Thesis_Project/main/All_DATA/without_sn_and_Epoch/EEG_HMC.csv'
dataset = pd.read_csv(data)

In [4]:
dataset.head()

Sleep Stage  MeanP_Alpha_F4  MedianF_Alpha_F4  MeanF_Alpha_F4  \
0           W         0.00051           8.74146        18.48195   
1           W         0.00040          10.24000        17.48293   
2           W         0.00036           9.74049        17.98244   
3           W         0.00035          10.11512        17.60780   
4           W         0.00033           9.74049        17.60780   

   Spectral Edge_Alpha_F4  PeakF_Alpha_F4  MeanP_Beta_F4  MedianF_Beta_F4  \
0                17.48293         8.24195        0.00071         19.73073   
1                16.85854        10.61463        0.00051         17.23317   
2                17.48293         8.74146        0.00047         17.60780   
3                17.10829         9.61561        0.00047         17.35805   
4                17.23317         8.11707        0.00043         17.23317   

   MeanF_Beta_F4  Spectral Edge_Beta_F4  ...  MeanP_Delta_O2  \
0       29.84585               33.84195  ...         0.00724   
1       26.34927               29.34634  ...         0.00723   
2       25.47512               28.22244  ...         0.00230   
3       26.47415               28.72195  ...         0.00091   
4       25.84976               28.09756  ...         0.00175   

   MedianF_Delta_O2  MeanF_Delta_O2  Spectral Edge_Delta_O2  PeakF_Delta_O2  \
0           0.74927         3.87122                 1.99805         0.87415   
1           0.49951         3.74634                 1.24878         0.49951   
2           0.62439         5.24488                 2.12293         0.62439   
3           0.87415         6.61854                 3.12195         0.62439   
4           0.49951         5.74439                 2.24780         0.49951   

   MeanP_Gamma_O2  MedianF_Gamma_O2  MeanF_Gamma_O2  Spectral Edge_Gamma_O2  \
0        0.000210          35.21561        42.20878                49.95122   
1        0.000095          34.34146        43.33268                49.95122   
2        0.000074          34.59122        45.95512                49.95122   
3        0.000082          32.46829        43.95707                49.95122   
4        0.000077          33.59220        44.83122                49.95122   

   PeakF_Gamma_O2  
0        49.95122  
1        49.95122  
2        49.95122  
3        49.95122  
4        49.95122  

[5 rows x 76 columns]

In [5]:
X = dataset.iloc[:, 1:].values
y = dataset.iloc[:, 0].values

In [6]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.33, random_state = 0)

In [7]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

In [8]:
from sklearn.neighbors import KNeighborsClassifier
KNN_class = KNeighborsClassifier(n_neighbors=3)
KNN_class.fit(X_train, y_train)
y_pred=KNN_class.predict(X_test)

In [9]:
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
print(confusion_matrix(y_test, y_pred))
print(classification_report(y_test,y_pred))
print("Accurecy: ",accuracy_score(y_test, y_pred))

[[ 1661  1072    49   448   677]
 [  913 10067  1228   572   191]
 [   58  1180  5715    20    34]
 [  455   676    46  4244    92]
 [  938   344    29    86  4994]]
              precision    recall  f1-score   support

          N1       0.41      0.43      0.42      3907
          N2       0.75      0.78      0.77     12971
          N3       0.81      0.82      0.81      7007
           R       0.79      0.77      0.78      5513
           W       0.83      0.78      0.81      6391

    accuracy                           0.75     35789
   macro avg       0.72      0.71      0.72     35789
weighted avg       0.75      0.75      0.75     35789

Accurecy:  0.7455083964346587


In [10]:
import pickle
pickle.dump(KNN_class,open('classifier.pkl','wb'))

In [11]:
!pip install lime

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [12]:
import lime
from lime import lime_tabular

In [13]:
import lime
from lime import lime_tabular

interpretor = lime_tabular.LimeTabularExplainer(
    training_data=np.array(X_train),
    feature_names=list(dataset.iloc[:0,1:]),
    mode='classification'
)

In [14]:
exp = interpretor.explain_instance(
    data_row=X_test[20], ##new data
    predict_fn=KNN_class.predict_proba
)

exp.show_in_notebook(show_table=True)

**Microsoft Library** 

In [15]:
!pip install interpret

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [16]:
from interpret.glassbox import ExplainableBoostingClassifier

ebm = ExplainableBoostingClassifier()
ebm.fit(X_train, y_train)

/usr/local/lib/python3.7/dist-packages/interpret/glassbox/ebm/ebm.py:922: UserWarning: Multiclass is still experimental. Subject to change per release.
  warn("Multiclass is still experimental. Subject to change per release.")
/usr/local/lib/python3.7/dist-packages/interpret/glassbox/ebm/ebm.py:925: UserWarning: Detected multiclass problem: forcing interactions to 0
  warn("Detected multiclass problem: forcing interactions to 0")


ExplainableBoostingClassifier(feature_names=['feature_0001', 'feature_0002',
                                             'feature_0003', 'feature_0004',
                                             'feature_0005', 'feature_0006',
                                             'feature_0007', 'feature_0008',
                                             'feature_0009', 'feature_0010',
                                             'feature_0011', 'feature_0012',
                                             'feature_0013', 'feature_0014',
                                             'feature_0015', 'feature_0016',
                                             'feature_0017', 'feature_0018',
                                             'feature_0019', 'feature_0020',
                                             'feat...
                                             'continuous', 'continuous',
                                             'continuous', 'continuous',
                              

In [17]:
from interpret import show

ebm_global = ebm.explain_global()
show(ebm_global)

/usr/local/lib/python3.7/dist-packages/interpret/provider/visualize.py:44: UserWarning: Cloud environment detected (['colab', 'ipython']): viz integration is still experimental.
  detected_envs
